In [19]:
%config Completer.use_jedi = False # tab 키 안먹을때

# BERT 기반 복합 토픽 모델(combined topic model)

## CTM 이란?
- 전통적인 빈도수 기반 문서 벡터화 방식인 `BoW(Bag of Words)`와 사전 훈련된 언어 모델의 문서 임베딩 방식인 `SBERT`를 결합하여 사용하는 복합 토픽 모델(Combined Topic Models, CTM)

In [6]:
# !pip install contextualized-topic-models==2.2.0
# !pip install pyldavis

     |████████████████████████████████| 121 kB 17.5 MB/s eta 0:00:01
     |████████████████████████████████| 79 kB 2.6 MB/s  eta 0:00:01
     |████████████████████████████████| 785 kB 82.4 MB/s eta 0:00:01
     |████████████████████████████████| 366 kB 85.0 MB/s eta 0:00:01
     |████████████████████████████████| 24.1 MB 75.6 MB/s eta 0:00:01     |██████████████████████████████▌ | 22.9 MB 75.6 MB/s eta 0:00:01
     |████████████████████████████████| 58 kB 1.3 MB/s s eta 0:00:01
     |████████████████████████████████| 128 kB 78.2 MB/s eta 0:00:01
     |████████████████████████████████| 128 kB 37.7 MB/s eta 0:00:01
     |████████████████████████████████| 128 kB 55.3 MB/s eta 0:00:01
     |████████████████████████████████| 127 kB 92.9 MB/s eta 0:00:01
     |████████████████████████████████| 126 kB 76.9 MB/s eta 0:00:01
     |████████████████████████████████| 126 kB 77.0 MB/s eta 0:00:01
     |████████████████████████████████| 125 kB 74.6 MB/s eta 0:00:01
     |████████████████████████████

     |████████████████████████████████| 3.8 MB 76.1 MB/s eta 0:00:01     |████▎                           | 512 kB 76.1 MB/s eta 0:00:01
     |████████████████████████████████| 24.8 MB 54.2 MB/s eta 0:00:01     |███████████████████████████████▌| 24.5 MB 54.2 MB/s eta 0:00:01
     |████████████████████████████████| 1.2 MB 39.2 MB/s eta 0:00:01
     |████████████████████████████████| 67 kB 1.7 MB/s  eta 0:00:01
     |████████████████████████████████| 6.5 MB 42.6 MB/s eta 0:00:01     |█████████▉                      | 2.0 MB 42.6 MB/s eta 0:00:01
     |████████████████████████████████| 895 kB 62.5 MB/s eta 0:00:01


  Using cached threadpoolctl-3.1.0-py3-none-any.whl (14 kB)
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.0-py3-none-any.whl size=120747 sha256=81699ae0017116b79394c731d3f15c622f6717725063e32902f44d5f749c9d71
  Stored in directory: /home/yeoai/.cache/pip/wheels/83/c0/df/b6873ab7aac3f2465aa9144b6b4c41c4391cfecc027c8b07e7
Successfully built sentence-transformers
  Attempting uninstall: ipython
    Found existing installation: ipython 7.32.0
    Uninstalling ipython-7.32.0:
      Successfully uninstalled ipython-7.32.0
  Attempting uninstall: ipykernel
    Found existing installation: ipykernel 6.9.2
    Uninstalling ipykernel-6.9.2:
      Successfully uninstalled ipykernel-6.9.2
  Attempting uninstall: ipywidgets
    Found existing installation: ipywidgets 7.6.5
    Uninstalling ipywidgets-7.6.5:
      Successfully uninstalled ipywidgets-7.6.5
     |████████████████████████████████| 1.7 MB 8.9 MB/s eta 0:00:01
  Installing build dependencies ... done
  Get

In [1]:
# data laod

!wget https://raw.githubusercontent.com/vinid/data/master/dbpedia_sample_abstract_20k_unprep.txt

--2022-03-16 14:09:16--  https://raw.githubusercontent.com/vinid/data/master/dbpedia_sample_abstract_20k_unprep.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 6208417 (5.9M) [text/plain]
Saving to: ‘dbpedia_sample_abstract_20k_unprep.txt’

dbpedia_sample_abst 100%[===================>]   5.92M  --.-KB/s    in 0.1s    

2022-03-16 14:09:17 (41.9 MB/s) - ‘dbpedia_sample_abstract_20k_unprep.txt’ saved [6208417/6208417]



In [2]:
!head -n 3 dbpedia_sample_abstract_20k_unprep.txt # 상위 3개 라인 출력

The Mid-Peninsula Highway is a proposed freeway across the Niagara Peninsula in the Canadian province of Ontario. Although plans for a highway connecting Hamilton to Fort Erie south of the Niagara Escarpment have surfaced for decades,it was not until The Niagara Frontier International Gateway Study was published by the Ministry
Monte Zucker (died March 15, 2007) was an American photographer. He specialized in wedding photography, entering it as a profession in 1947. In the 1970s he operated a studio in Silver Spring, Maryland. Later he lived in Florida. He was Brides Magazine's Wedding Photographer of the Year for 1990 and
Henry Howard, 13th Earl of Suffolk, 6th Earl of Berkshire (8 August 1779 – 10 August 1779) was a British peer, the son of Henry Howard, 12th Earl of Suffolk. His father died on 7 March 1779, leaving behind his pregnant widow. The Earldom of Suffolk became dormant until she


In [3]:
text_file = "dbpedia_sample_abstract_20k_unprep.txt" # 파일명 변수로 저장

## 전처리

In [9]:
from contextualized_topic_models.models.ctm import CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation
from contextualized_topic_models.utils.preprocessing import WhiteSpacePreprocessing
import nltk

In [10]:
# Bag of Words 기반 접근에서는 전처리 챕터에서 학습했던 정규화 과정이 상당히 중요함
# -> nltk에서 제공하는 불용어 처리, 특수문자 제거, 영단어 소문자화 진행
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /home/yeoai/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [11]:
documents = [line.strip() for line in open(text_file, encoding='utf-8').readlines()]
sp = WhiteSpacePreprocessing(documents, stopwords_language='english')
preprocessed_documents, unpreprocessed_corpus, vocab = sp.preprocess()

/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [12]:
# 전처리 전
unpreprocessed_corpus[:2]

['The Mid-Peninsula Highway is a proposed freeway across the Niagara Peninsula in the Canadian province of Ontario. Although plans for a highway connecting Hamilton to Fort Erie south of the Niagara Escarpment have surfaced for decades,it was not until The Niagara Frontier International Gateway Study was published by the Ministry',
 "Monte Zucker (died March 15, 2007) was an American photographer. He specialized in wedding photography, entering it as a profession in 1947. In the 1970s he operated a studio in Silver Spring, Maryland. Later he lived in Florida. He was Brides Magazine's Wedding Photographer of the Year for 1990 and"]

In [13]:
# normalization 후 문서
preprocessed_documents[:2]

['mid peninsula highway proposed across peninsula canadian province ontario although highway connecting hamilton fort south international study published ministry',
 'died march american photographer specialized photography operated studio silver spring maryland later lived florida magazine photographer year']

In [14]:
# 전체 단어 집합 크기
print('BOW에 사용될 단어 집합 크기:', len(vocab)) #  WhiteSpacePreprocessing()의 vocabulary_size 인자의 기본값이 2000임.

BOW에 사용될 단어 집합 크기: 2000


In [15]:
tp = TopicModelDataPreparation('paraphrase-distilroberta-base-v1') # pretrained BERT model
training_dataset = tp.fit(text_for_contextual=unpreprocessed_corpus, text_for_bow=preprocessed_documents)

Downloading:   0%|          | 0.00/391 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/3.74k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/718 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/122 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/456k [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/1.35k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/798k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/100 [00:00<?, ?it/s]

/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [16]:
len(tp.vocab)

2000

## Combined TM 학습

In [17]:
ctm = CombinedTM(bow_size=len(tp.vocab), contextual_size=768, n_components=50,
                num_epochs=20)
ctm.fit(training_dataset)

0it [00:00, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Epoch: [1/20]	 Seen Samples: [20000/400000]	Train Loss: 160.7985130371094	Time: 0:00:01.923661: : 1it [00:01,  1.92s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Epoch: [2/20]	 Seen Samples: [40000/400000]	Train Loss: 144.36200554199218	Time: 0:00:01.734937: : 2it [00:03,  1.81s/it]

...

Epoch: [18/20]	 Seen Samples: [360000/400000]	Train Loss: 135.921953515625	Time: 0:00:01.847657: : 18it [00:33,  1.84s/it]  

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Epoch: [19/20]	 Seen Samples: [380000/400000]	Train Loss: 135.83132534179688	Time: 0:00:01.841385: : 19it [00:34,  1.84s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Epoch: [20/20]	 Seen Samples: [400000/400000]	Train Loss: 135.75406208496094	Time: 0:00:01.832185: : 20it [00:36,  1.84s/it]


## 결과 출력

In [18]:
ctm.get_topic_lists(5)

[['published', 'book', 'books', 'art', 'award'],
 ['road', 'bridge', 'line', 'river', 'railway'],
 ['held', 'party', 'council', 'members', 'election'],
 ['university', 'professor', 'law', 'received', 'born'],
 ['family', 'found', 'brown', 'mm', 'moth'],
 ['league', 'played', 'club', 'football', 'team'],
 ['located', 'national', 'house', 'historic', 'built'],
 ['band', 'released', 'music', 'album', 'rock'],
 ['station', 'line', 'railway', 'located', 'city'],
 ['best', 'known', 'film', 'american', 'actress'],
 ['studied', 'painter', 'french', 'january', 'paris'],
 ['album', 'released', 'first', 'live', 'studio'],
 ['series', 'game', 'video', 'developed', 'television'],
 ['located', 'town', 'miles', 'area', 'river'],
 ['de', 'century', 'published', 'book', 'french'],
 ['television', 'company', 'owned', 'radio', 'channel'],
 ['considered', 'planet', 'languages', 'ancient', 'given'],
 ['population', 'province', 'district', 'town', 'area'],
 ['used', 'using', 'system', 'developed', 'product'

In [19]:
## 시각화(pyLDAvis)
lda_vis_data =ctm.get_ldavis_data_format(tp.vocab, training_dataset,n_samples=10)

0it [00:00, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [1/10]: : 1it [00:00,  1.03it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [2/10]: : 2it [00:02,  1.04s/it]

...

Sampling: [8/10]: : 8it [00:08,  1.04s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [9/10]: : 9it [00:09,  1.04s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [10/10]: : 10it [00:10,  1.04s/it]


In [ ]:
import pyLDAvis as vis

lad_vis_data = ctm.get_ldavis_data_format(tp.vocab, training_dataset, n_samples=10)

ctm_pd = vis.prepare(**lda_vis_data)

In [26]:
vis.display(ctm_pd)

## 예측

In [21]:
import numpy as np

In [22]:
topics_predictions = ctm.get_thetas(training_dataset, n_samples=5)
# get all topic predictions

0it [00:00, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [1/5]: : 1it [00:01,  1.01s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [2/5]: : 2it [00:02,  1.06s/it]

...

Sampling: [3/5]: : 3it [00:03,  1.05s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [4/5]: : 4it [00:04,  1.04s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Sampling: [5/5]: : 5it [00:05,  1.05s/it]


In [23]:
# 전처리 문서의 첫번째 문서
print(preprocessed_documents[0])

mid peninsula highway proposed across peninsula canadian province ontario although highway connecting hamilton fort south international study published ministry


In [30]:
ctm.get_topic_lists(5)[4]

['family', 'found', 'brown', 'mm', 'moth']

## 모델 저장 및 로드

In [31]:
ctm.save(models_dir='./')

del ctm

/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/contextualized_topic_models/models/ctm.py:472: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  Warning)


In [34]:
ctm = CombinedTM(bow_size=len(tp.vocab), contextual_size=768, num_epochs=100, n_components=50)

ctm.load('./contextualized_topic_model_nc_50_tpm_0.0_tpv_0.98_hs_prodLDA_ac_(100, 100)_do_softplus_lr_0.2_mo_0.002_rp_0.99',
        epoch=19)

/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/contextualized_topic_models/models/ctm.py:497: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  Warning)


In [35]:
ctm.get_topic_lists(5)

[['published', 'book', 'books', 'art', 'award'],
 ['road', 'bridge', 'line', 'river', 'railway'],
 ['held', 'party', 'council', 'members', 'election'],
 ['university', 'professor', 'law', 'received', 'born'],
 ['family', 'found', 'brown', 'mm', 'moth'],
 ['league', 'played', 'club', 'football', 'team'],
 ['located', 'national', 'house', 'historic', 'built'],
 ['band', 'released', 'music', 'album', 'rock'],
 ['station', 'line', 'railway', 'located', 'city'],
 ['best', 'known', 'film', 'american', 'actress'],
 ['studied', 'painter', 'french', 'january', 'paris'],
 ['album', 'released', 'first', 'live', 'studio'],
 ['series', 'game', 'video', 'developed', 'television'],
 ['located', 'town', 'miles', 'area', 'river'],
 ['de', 'century', 'published', 'book', 'french'],
 ['television', 'company', 'owned', 'radio', 'channel'],
 ['considered', 'planet', 'languages', 'ancient', 'given'],
 ['population', 'province', 'district', 'town', 'area'],
 ['used', 'using', 'system', 'developed', 'product'

/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/home/yeoai/anaconda3/envs/pytorch/lib/pytho

- https://wikidocs.net/161310

---

# BERT 기반 한국어 복합 토픽 모델

In [37]:
# !pip install konlpy

In [38]:
# data 
!wget https://raw.githubusercontent.com/lovit/soynlp/master/tutorials/2016-10-20.txt

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
--2022-03-16 14:46:23--  https://raw.githubusercontent.com/lovit/soynlp/master/tutorials/2016-10-20.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 43694449 (42M) [text/plain]
Saving to: ‘2016-10-20.txt’

2016-10-20.txt      100%[===================>]  41.67M  49.1MB/s    in 0.8s    

2022-03-16 14:46:28 (49.1 MB/s) - ‘2016-10-20.txt’ saved [43694449/43694449]



In [39]:
!head -n 1 2016-10-20.txt

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
 


In [45]:
# !head -n 3 2016-10-20.txt

In [4]:
text_file = "2016-10-20.txt"

In [5]:
from contextualized_topic_models.models.ctm import CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation, bert_embeddings_from_list
from contextualized_topic_models.utils.preprocessing import WhiteSpacePreprocessing
from sklearn.feature_extraction.text import CountVectorizer
from konlpy.tag import Mecab
from tqdm import tqdm

In [6]:
# prerpocessing

documents = [line.strip() for line in open(text_file, encoding="utf-8").readlines()]
documents[:5]

['',
 '19  1990  52 1 22',
 '오패산터널 총격전 용의자 검거 서울 연합뉴스 경찰 관계자들이 19일 오후 서울 강북구 오패산 터널 인근에서 사제 총기를 발사해 경찰을 살해한 용의자 성모씨를 검거하고 있다 성씨는 검거 당시 서바이벌 게임에서 쓰는 방탄조끼에 헬멧까지 착용한 상태였다 독자제공 영상 캡처 연합뉴스  서울 연합뉴스 김은경 기자 사제 총기로 경찰을 살해한 범인 성모 46 씨는 주도면밀했다  경찰에 따르면 성씨는 19일 오후 강북경찰서 인근 부동산 업소 밖에서 부동산업자 이모 67 씨가 나오기를 기다렸다 이씨와는 평소에도 말다툼을 자주 한 것으로 알려졌다  이씨가 나와 걷기 시작하자 성씨는 따라가면서 미리 준비해온 사제 총기를 이씨에게 발사했다 총알이 빗나가면서 이씨는 도망갔다 그 빗나간 총알은 지나가던 행인 71 씨의 배를 스쳤다  성씨는 강북서 인근 치킨집까지 이씨 뒤를 쫓으며 실랑이하다 쓰러뜨린 후 총기와 함께 가져온 망치로 이씨 머리를 때렸다  이 과정에서 오후 6시 20분께 강북구 번동 길 위에서 사람들이 싸우고 있다 총소리가 났다 는 등의 신고가 여러건 들어왔다  5분 후에 성씨의 전자발찌가 훼손됐다는 신고가 보호관찰소 시스템을 통해 들어왔다 성범죄자로 전자발찌를 차고 있던 성씨는 부엌칼로 직접 자신의 발찌를 끊었다  용의자 소지 사제총기 2정 서울 연합뉴스 임헌정 기자 서울 시내에서 폭행 용의자가 현장 조사를 벌이던 경찰관에게 사제총기를 발사해 경찰관이 숨졌다 19일 오후 6시28분 강북구 번동에서 둔기로 맞았다 는 폭행 피해 신고가 접수돼 현장에서 조사하던 강북경찰서 번동파출소 소속 김모 54 경위가 폭행 용의자 성모 45 씨가 쏜 사제총기에 맞고 쓰러진 뒤 병원에 옮겨졌으나 숨졌다 사진은 용의자가 소지한 사제총기  신고를 받고 번동파출소에서 김창호 54 경위 등 경찰들이 오후 6시 29분께 현장으로 출동했다 성씨는 그사이 부동산 앞에 놓아뒀던 가방을 챙겨 오패산 쪽으로 도망간 후였다  김 경위는 오패산 터널 입구 오른쪽

In [7]:
not '19  1990  52 1 22'.replace(' ', '').isdecimal()

False

In [8]:
preprocessed_documents = []

for line in tqdm(documents) :
    # 빈 문자열이거나 숫자로만 이루어진 좋은 제외
    if line and not line.replace(' ', '').isdecimal() :
        preprocessed_documents.append(line)

100%|██████████| 30091/30091 [00:00<00:00, 262234.42it/s]


In [9]:
len(preprocessed_documents)

27540

In [15]:
class CustomTokenizer :
    def __init__(self, tagger) :
        self.tagger = tagger
        
    def __call__(self, sent) :
        word_tokens = self.tagger.morphs(sent)
        result = [word for word in word_tokens if len(word) > 1]
        return result
    
custom_tokenizer = CustomTokenizer(Mecab())

In [17]:
vectorizer = CountVectorizer(tokenizer=custom_tokenizer, max_features=3000)

In [18]:
train_bow_embeddings = vectorizer.fit_transform(preprocessed_documents)

In [20]:
print(train_bow_embeddings.shape)

(27540, 3000)


In [21]:
vocab = vectorizer.get_feature_names()
id2token = {k : v for k, v in zip(range(0, len(vocab)), vocab)}

/home/yeoai/anaconda3/envs/pytorch/lib/python3.7/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [22]:
len(vocab)

3000

In [25]:
train_contextualized_embeddings = bert_embeddings_from_list(preprocessed_documents, \
                                                            'sentence-transformers/xlm-r-100langs-bert-base-nli-stsb-mean-tokens')

Batches:   0%|          | 0/138 [00:00<?, ?it/s]

In [26]:
qt = TopicModelDataPreparation()

train_dataset = qt.load(train_contextualized_embeddings, train_bow_embeddings, id2token)

## combinedTM 학습하기

In [28]:
ctm = CombinedTM(bow_size=len(vocab), contextual_size=768, n_components=50, num_epochs=20)
ctm.fit(train_dataset)

Epoch: [20/20]	 Seen Samples: [550800/550800]	Train Loss: 849.8584591446532	Time: 0:00:02.780976: : 20it [00:57,  2.86s/it]


In [29]:
ctm.get_topics(5)

defaultdict(list,
            {0: ['대표', '갤러리', '민주당', '의원', '탈당'],
             1: ['뉴시스', '영상', '공감', '제보', '언론'],
             2: ['공개', '화보', '그램', '눈길', '조안'],
             3: ['원전', '편입', '한전', '기업', '수주'],
             4: ['공제', '정산', '연말', '소득', '미리'],
             5: ['영화제', '영화', '에서', '관객', '한국'],
             6: ['가계', '이자', '금리', '대출', '순이익'],
             7: ['교육', '학생', '진로', '박람회', '교육청'],
             8: ['타임', '스퀘어', '제작', '하늘', '발표회'],
             9: ['화신', '정원', '나리', '질투', '루이'],
             10: ['습니다', '다고', '라고', '사람', '에서'],
             11: ['지하', '임대', '지상', '전용', '면적'],
             12: ['중구', '패션', '디자인', '2017', '컬렉션'],
             13: ['뉴시스', '영상', '공감', '언론', '제보'],
             14: ['경찰', '경찰관', '총기', '사제', '터널'],
             15: ['유용', '대통령', '스포츠', '불법행위', '미르'],
             16: ['친환경', '시흥', '경력', '채용', '산업'],
             17: ['스크린', '전동차', '출입문', '도어', '으로'],
             18: ['네이버', '의장', '대표', '한성숙', '이사회'],
             19: ['출시', '스토어', '플레

In [30]:
import pyLDAvis as vis

lda_vis_data = ctm.get_ldavis_data_format(vocab, train_dataset, n_samples=10)

ctm_pd = vis.prepare(**lda_vis_data)
vis.display(ctm_pd)

Sampling: [10/10]: : 10it [00:14,  1.44s/it]
